In [ ]:
import pandas as pd
import scipy.io as sio
from scipy import signal
from scipy import stats
import numpy as np
import datetime
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import re

downRiverDF = pd.read_csv('downriver_2013_2014_processed.csv', parse_dates = ['DN'])
correlation = signal.correlate(downRiverDF["BottomPressure"].ffill().bfill().to_numpy(), downRiverDF["SurfaceSalCorrected"].ffill().bfill().to_numpy(), mode="full")
lags = signal.correlation_lags(downRiverDF["BottomPressure"].ffill().bfill().to_numpy().size, downRiverDF["SurfaceSalCorrected"].ffill().bfill().to_numpy().size, mode="full") 
lag = lags[np.argmax(correlation)]
res = stats.pearsonr(downRiverDF["BottomPressure"].ffill().bfill().to_numpy(), downRiverDF["SurfaceSalCorrected"].ffill().bfill().to_numpy())
print(lag)
print(res)


minilanderDF = pd.read_csv('minilander_2013_2014_processed.csv', parse_dates = ['DN'])

# USING SURFACE SALINITY DUE TO POOR BOTTOM SALNITY DATA

#create day DN to separate out data values by day instead of 5 min intervals
downRiverDF['dayDN'] = downRiverDF['DN'].dt.floor('D')
minilanderDF['dayDN'] = minilanderDF['DN'].dt.floor('D')
#takes highest sal values by day and collects idx, then converts floats to integers
idxMaxDownArray = downRiverDF.groupby("dayDN")["SurfaceSalCorrected"].idxmax().ffill().astype('Int64').to_numpy()
idxMaxMiniArray = minilanderDF.groupby("dayDN")["Salinity"].idxmax().ffill().bfill().astype('Int64').to_numpy()

#filter data frame from NAN duplicates created in previous step
salToTempDownDF = downRiverDF.loc[idxMaxDownArray].drop_duplicates()
salToTempMiniDF = minilanderDF.loc[idxMaxMiniArray].drop_duplicates()

#trying to combine so that both arrays are same length
combinedDF = pd.merge_asof(salToTempDownDF, salToTempMiniDF, on = 'DN')[["DN", "SurfaceTemp", "Temperature", "SurfaceSalCorrected", "Salinity"]]
maxDN = combinedDF["DN"].max()
# adding empty columns to allow for concat to work
salToTempMiniDF["SurfaceTemp"] = np.nan
salToTempMiniDF["SurfaceSalCorrected"] = np.nan
#combining tail of minilander data to other data
combinedDF = pd.concat([combinedDF, salToTempMiniDF.loc[salToTempMiniDF['DN']>maxDN][["DN", "SurfaceTemp", "Temperature", "SurfaceSalCorrected", "Salinity"]]])

#STONEWALL BANK OCEAN TEMPERATURE
stonewallDF = pd.concat([pd.read_csv('2013_2014_stonewallbank.csv'), pd.read_csv('2014_stonewall.csv')])
# format time series
stonewallDF["dayDN"] = (pd.to_datetime(stonewallDF['YY'].astype(str) + '/' + stonewallDF['MM'].astype(str) + '/' + stonewallDF['DD'].astype(str) + '/' , format='mixed'))
# isolate and group by average value for that day
dailyStonewallDF = stonewallDF.groupby("dayDN").agg(dailyAverage = ("WTMP", "mean")).reset_index()
# get the time series to be the same size
combinedDF = pd.merge_asof(combinedDF, dailyStonewallDF, left_on = "DN", right_on = "dayDN")
#plot ocean temperature
tempFigLabels = ['SurfaceTempAtMaxSal', 'MiniTempAtMaxSal', 'SurfaceSal', 'MiniSal', 'Stonewall Bank']
tempfig = px.line(x = combinedDF['DN'], y = [combinedDF["SurfaceTemp"], combinedDF["Temperature"], combinedDF['SurfaceSalCorrected'], combinedDF['Salinity'], combinedDF["dailyAverage"]] , color_discrete_sequence= ["black", "purple", "navy","orange", "red"], title = "Temperature/Salinity", markers = True)
for idx in range(len(tempFigLabels)):
    tempfig.data[idx].name = tempFigLabels[idx]
    tempfig.data[idx].hovertemplate = 'variable=' + tempFigLabels[idx] + '<br>x=%{x}<br>value=%{y}<extra></extra>'
    tempfig.data[idx].legendgroup = tempFigLabels[idx]
tempfig.update_layout(xaxis_title="Date", yaxis_title="Temperature (°C)/Salinity", legend_title="Locations")
tempfig.update_layout(title=dict(text= "Ocean Temperature and Salinity for 2013-2014", font=dict(size=25)))
tempfig.update_xaxes(tickangle=30)
tempfig.update_xaxes(rangeslider_visible=True)
tempfig.update_xaxes(range = [pd.Timestamp('2013-10-30'),pd.Timestamp('2014-03-13')])
tempfig.show() 

#bottom pressure and surface salinity combined plot 
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Scatter(x=downRiverDF['DN'], y= downRiverDF['SurfaceSalCorrected'], name="Surface Salinity"),secondary_y=False,)
fig.add_trace(go.Scatter(x=downRiverDF['DN'], y=downRiverDF['BottomPressure'], name="Bottom Pressure"),secondary_y=True,)
fig.update_layout(title_text="Sea Level and Salinity")
fig.update_xaxes(title_text="Date")
fig.update_yaxes(title_text="Surface Salinity", secondary_y=False)
fig.update_yaxes(title_text="Bottom Pressure", secondary_y=True)
fig.show()



0
PearsonRResult(statistic=np.float64(0.5840946197302562), pvalue=np.float64(0.0))


: 